In [191]:
import pandas as pd
import plotly.express as px
import numpy as np

df = pd.read_csv('https://opendata.ecdc.europa.eu/covid19/casedistribution/csv')
df["dateRep"] = pd.to_datetime(df["dateRep"],infer_datetime_format=True)\
        .dt.strftime('%B, %d, %Y')

df = df.sort_values(by=["year","month","day"])
df['Cases_cumulative'] = df.groupby(['countriesAndTerritories'])['cases'].cumsum()
df["Cases_cumulative_rel"] = df["Cases_cumulative"] / df["popData2018"] * 100
df

dateRep  day  month  year  cases  deaths  \
80    December, 31, 2019   31     12  2019      0       0   
218   December, 31, 2019   31     12  2019      0       0   
335   December, 31, 2019   31     12  2019      0       0   
435   December, 31, 2019   31     12  2019      0       0   
526   December, 31, 2019   31     12  2019      0       0   
...                  ...  ...    ...   ...    ...     ...   
7570     March, 30, 2020   30      3  2020     12       0   
7585     March, 30, 2020   30      3  2020      0       0   
7601     March, 30, 2020   30      3  2020      5       0   
7688     March, 30, 2020   30      3  2020      1       0   
7700     March, 30, 2020   30      3  2020      0       0   

     countriesAndTerritories geoId countryterritoryCode  popData2018  \
80               Afghanistan    AF                  AFG   37172386.0   
218                  Algeria    DZ                  DZA   42228429.0   
335                  Armenia    AM                  ARM    2951776.0   
435                Australia    AU                  AUS   24992369.0   
526                  Austria    AT                  AUT    8847037.0   
...                      ...   ...                  ...          ...   
7570              Uzbekistan    UZ                  UZB   32955400.0   
7585               Venezuela    VE                  VEN   28870195.0   
7601                 Vietnam    VN                  VNM   95540395.0   
7688                  Zambia    ZM                  ZMB   17351822.0   
7700                Zimbabwe    ZW                  ZWE   14439018.0   

      Cases_cumulative  Cases_cumulative_rel  
80                   0              0.000000  
218                  0              0.000000  
335                  0              0.000000  
435                  0              0.000000  
526                  0              0.000000  
...                ...                   ...  
7570               145              0.000440  
7585               119              0.000412  
7601               228              0.000239  
7688                29              0.000167  
7700                 7              0.000048  

[7710 rows x 12 columns]

In [ ]:
# plot ideas:
"""
- normalized plot to compare all countries (like a joy plot maybe?! -> compare curves)
- can area under plot show how well a country tests or is it the same accross countries?!
- cloropleth plot

"""

In [38]:
px.line(df.query("geoId=='AT'"),x="dateRep",y="Cases_cumulative")

In [ ]:
'''TODO:
- all countries should appear for each date
- fillna if necessary
'''

In [192]:
"this cell takes around 1 min 16sec..."
countries = df.countriesAndTerritories.unique()
dates = df.dateRep.unique() # all measurements need all countries, even if they 0's
for date in dates:
    df_date = df[df.dateRep==date]
    day, month, year = df_date.day.unique(), df_date.month.unique(), df_date.year.unique()
    countries_date = df_date.countriesAndTerritories.unique()
    for missing_country in set(countries) - set(countries_date):
        df_tmp = df[df.countriesAndTerritories==missing_country].head(1) # get sample data
        df_tmp["dateRep"] = date
        df_tmp["cases"], df_tmp["deaths"] = [0, 0]
        df_tmp["Cases_cumulative"], df_tmp["Cases_cumulative_rel"] = [0, 0]
        df_tmp["day"], df_tmp["month"], df_tmp["year"] = day, month, year
        df=df.append(df_tmp)

df

dateRep  day  month  year  cases  deaths  \
80    December, 31, 2019   31     12  2019      0       0   
218   December, 31, 2019   31     12  2019      0       0   
335   December, 31, 2019   31     12  2019      0       0   
435   December, 31, 2019   31     12  2019      0       0   
526   December, 31, 2019   31     12  2019      0       0   
...                  ...  ...    ...   ...    ...     ...   
5834     March, 27, 2020   27      3  2020      0       0   
1417     March, 27, 2020   27      3  2020      0       0   
1417     March, 28, 2020   28      3  2020      0       0   
1417     March, 29, 2020   29      3  2020      0       0   
1417     March, 30, 2020   30      3  2020      0       0   

                         countriesAndTerritories     geoId  \
80                                   Afghanistan        AF   
218                                      Algeria        DZ   
335                                      Armenia        AM   
435                                    Australia        AU   
526                                      Austria        AT   
...                                          ...       ...   
5834                                 Puerto_Rico        PR   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   

     countryterritoryCode  popData2018  Cases_cumulative  Cases_cumulative_rel  
80                    AFG   37172386.0                 0                   0.0  
218                   DZA   42228429.0                 0                   0.0  
335                   ARM    2951776.0                 0                   0.0  
435                   AUS   24992369.0                 0                   0.0  
526                   AUT    8847037.0                 0                   0.0  
...                   ...          ...               ...                   ...  
5834                  PRI    3195153.0                 0                   0.0  
1417                  NaN       3000.0                 0                   0.0  
1417                  NaN       3000.0                 0                   0.0  
1417                  NaN       3000.0                 0                   0.0  
1417                  NaN       3000.0                 0                   0.0  

[17836 rows x 12 columns]

In [150]:
fig = px.choropleth(df, locations="countryterritoryCode",
                    color="Cases_cumulative", # lifeExp is a column of gapminder
                    animation_frame="dateRep",
                    range_color=(0,8000),
                    hover_name="countriesAndTerritories", # column to add to hover information
                    color_continuous_scale=px.colors.sequential.Plasma)

fig.show()

In [79]:
df

dateRep  cases  deaths  \
6969  December, 31, 2019      0       0   
2375  December, 31, 2019      0       0   
4234  December, 31, 2019      0       0   
2252  December, 31, 2019      0       0   
7350  December, 31, 2019      0       0   
...                  ...    ...     ...   
5834     March, 27, 2020      0       0   
1417     March, 27, 2020      0       0   
1417     March, 28, 2020      0       0   
1417     March, 29, 2020      0       0   
1417     March, 30, 2020      0       0   

                         countriesAndTerritories     geoId  \
6969                                 Switzerland        CH   
2375                                     Estonia        EE   
4234                                     Lebanon        LB   
2252                                       Egypt        EG   
7350                        United_Arab_Emirates        AE   
...                                          ...       ...   
5834                                 Puerto_Rico        PR   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   
1417  Cases_on_an_international_conveyance_Japan  JPG11668   

     countryterritoryCode  popData2018  Cases_cumulative  
6969                  CHE    8516543.0                 0  
2375                  EST    1320884.0                 0  
4234                  LBN    6848925.0                 0  
2252                  EGY   98423595.0                 0  
7350                  ARE    9630959.0                 0  
...                   ...          ...               ...  
5834                  PRI    3195153.0                 0  
1417                  NaN       3000.0                 0  
1417                  NaN       3000.0                 0  
1417                  NaN       3000.0                 0  
1417                  NaN       3000.0                 0  

[17836 rows x 8 columns]

In [85]:
print(df.Cases_cumulative_rel.to_string())

6969    0.000000e+00
2375    0.000000e+00
4234    0.000000e+00
2252    0.000000e+00
7350    0.000000e+00
2516    0.000000e+00
5424    0.000000e+00
713     0.000000e+00
3199    0.000000e+00
7546    0.000000e+00
6878    0.000000e+00
6010    0.000000e+00
1089    0.000000e+00
5057    0.000000e+00
7687    0.000000e+00
7441    0.000000e+00
3373    0.000000e+00
2737    0.000000e+00
80      0.000000e+00
2165    0.000000e+00
4697    0.000000e+00
1417    0.000000e+00
4356    0.000000e+00
435     0.000000e+00
6677    0.000000e+00
4540    0.000000e+00
7066    0.000000e+00
2607    0.000000e+00
4105    0.000000e+00
3642    0.000000e+00
218     0.000000e+00
1234    0.000000e+00
825     0.000000e+00
5595    0.000000e+00
2945    0.000000e+00
3464    0.000000e+00
1343    0.000000e+00
5778    0.000000e+00
6230    0.000000e+00
1977    0.000000e+00
916     0.000000e+00
6404    0.000000e+00
7150    0.000000e+00
335     0.000000e+00
1734    0.000000e+00
5251    0.000000e+00
1571    1.938639e-08
5149    0.000

In [211]:
#px.choropleth.__code__.co_varnames
fig = px.choropleth(df, locations="countryterritoryCode",
                    color="Cases_cumulative_rel", # lifeExp is a column of gapminder
                    animation_frame="dateRep",
                    range_color=(0,0.08),
                    hover_name="countriesAndTerritories", # column to add to hover information
                    color_continuous_scale=px.colors.sequential.Plasma)



In [212]:
fig.show()

In [ ]:
"""next: racing bar chart of relative cases (top 10)"""

In [210]:
cond1=df["countriesAndTerritories"]=="Switzerland"
cond2=df["countriesAndTerritories"]=="Austria"
cond3=df["countriesAndTerritories"]=="Germany"
cond4=df["countriesAndTerritories"]=="Sweden"
cond5=df["countriesAndTerritories"]=="France"
cond6=df["countriesAndTerritories"]=="Italy"
cond7=df["countriesAndTerritories"]=="Spain"
cond8=df["countriesAndTerritories"]=="United_Kingdom"
cond9=df["countriesAndTerritories"]=="Iceland"
cond10=df["countriesAndTerritories"]=="Belgium"

df_filtered = df[cond1 | cond2 | cond3 | cond4 | cond5 | cond6 | cond7 | cond8 | cond9 | cond10]

fig = px.bar(df_filtered.sort_values(by=["year","month","day","Cases_cumulative_rel"],
                                    ascending=[True, True, True, False]),
             x="countriesAndTerritories", y="Cases_cumulative_rel", 
             color = "countriesAndTerritories",
             text = "Cases_cumulative",
             animation_frame="dateRep",
             #hover_data=["cases"],
            )
            
fig.update_yaxes(range=(0, 0.3),title="rel. cumulative cases [%]")
fig.update_xaxes(title="Country")
fig.update_traces(textposition="inside")
fig.update_layout(showlegend=False)

In [208]:
fig.show()

In [20]:
df_filtered=df.query("countriesAndTerritories=='Switzerland'").sort_values(by="DateRep")
max_count = df_filtered.cases.max()
df_filtered.cases /= max_count 
max_cumcount = df_filtered.Cases_cumulative.max()
fig=px.line(df_filtered, x="DateRep", y="cases")
fig.add_scatter(x=df_filtered.DateRep, y=df_filtered.Cases_cumulative/max_cumcount)


In [11]:
df_filtered

dateRep  day  month  year  cases  deaths countriesAndTerritories  \
526  31/12/2019   31     12  2019      0       0                 Austria   
494  01/02/2020    1      2  2020      0       0                 Austria   
493  02/02/2020    2      2  2020      0       0                 Austria   
492  03/02/2020    3      2  2020      0       0                 Austria   
491  04/02/2020    4      2  2020      0       0                 Austria   
..          ...  ...    ...   ...    ...     ...                     ...   
440  26/03/2020   26      3  2020    606       4                 Austria   
439  27/03/2020   27      3  2020   1141      18                 Austria   
438  28/03/2020   28      3  2020    668      16                 Austria   
437  29/03/2020   29      3  2020    594       0                 Austria   
436  30/03/2020   30      3  2020    522      18                 Austria   

    geoId countryterritoryCode  popData2018             DateRep  \
526    AT                  AUT    8847037.0  December, 31, 2019   
494    AT                  AUT    8847037.0  February, 01, 2020   
493    AT                  AUT    8847037.0  February, 02, 2020   
492    AT                  AUT    8847037.0  February, 03, 2020   
491    AT                  AUT    8847037.0  February, 04, 2020   
..    ...                  ...          ...                 ...   
440    AT                  AUT    8847037.0     March, 26, 2020   
439    AT                  AUT    8847037.0     March, 27, 2020   
438    AT                  AUT    8847037.0     March, 28, 2020   
437    AT                  AUT    8847037.0     March, 29, 2020   
436    AT                  AUT    8847037.0     March, 30, 2020   

     Cases_cumulative  
526                 0  
494                 0  
493                 0  
492                 0  
491                 0  
..                ...  
440              5888  
439              7029  
438              7697  
437              8291  
436              8813  

[91 rows x 12 columns]